<a href="https://colab.research.google.com/github/MJ199999/Car-Detecting/blob/main/CarDetection.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 구글 드라이브 마운트

In [2]:
from google.colab import drive
drive.mount('/gdrive')
drive.mount('/content/drive')


Mounted at /gdrive
Mounted at /content/drive


# 임포트

In [3]:
import cv2
import matplotlib.pyplot as plt
import glob

# Darknet 다운받아서 컴파일

In [4]:
!git clone https://github.com/AlexeyAB/darknet.git

Cloning into 'darknet'...
remote: Enumerating objects: 15521, done.
remote: Counting objects: 100% (7/7), done.
remote: Compressing objects: 100% (7/7), done.
remote: Total 15521 (delta 0), reused 5 (delta 0), pack-reused 15514
Receiving objects: 100% (15521/15521), 14.19 MiB | 10.56 MiB/s, done.
Resolving deltas: 100% (10412/10412), done.


In [5]:
%cd darknet

/content/darknet


In [6]:
!sed -i 's/OPENCV=0/OPENCV=1/' Makefile
!sed -i 's/GPU=0/GPU=1/' Makefile
!sed -i 's/CUDNN=0/CUDNN=1/' Makefile
!sed -i 's/CUDNN_HALF=0/CUDNN_HALF=1' Makefile
!sed -i 's/LIBSO=0/LIBSO=1' Makefile

!make

sed: -e expression #1, char 27: unterminated `s' command
sed: -e expression #1, char 17: unterminated `s' command
mkdir -p ./obj/
mkdir -p backup
chmod +x *.sh
g++ -std=c++11 -std=c++11 -Iinclude/ -I3rdparty/stb/include -DOPENCV `pkg-config --cflags opencv4 2> /dev/null || pkg-config --cflags opencv` -DGPU -I/usr/local/cuda/include/ -DCUDNN -Wall -Wfatal-errors -Wno-unused-result -Wno-unknown-pragmas -fPIC -rdynamic -Ofast -DOPENCV -DGPU -DCUDNN -I/usr/local/cudnn/include -c ./src/image_opencv.cpp -o obj/image_opencv.o
./src/image_opencv.cpp: In function ‘void draw_detections_cv_v3(void**, detection*, int, float, char**, image**, int, int)’:
./src/image_opencv.cpp:946:23: warning: variable ‘rgb’ set but not used [-Wunused-but-set-variable]
  946 |                 float rgb[3];
      |                       ^~~
./src/image_opencv.cpp: In function ‘void draw_train_loss(char*, void**, int, float, float, int, int, float, int, char*, float, int, int, double)’:
./src/image_opencv.cpp:1147:13

# Annotation을 yolo 형식으로 바꾸기

In [7]:
import glob
import os
import cv2
from tqdm import tqdm
import shutil
import math

In [ ]:
txt_file_list = glob.glob('/content/drive/MyDrive/CarData/valid/*.txt')

In [ ]:
for file in tqdm(txt_file_list):
    file_name = os.path.basename(file)
    file_name = file_name.split('.')[0]
    img = cv2.imread('/content/drive/MyDrive/CarData/valid/' + file_name + '.jpg')
    img_height, img_width, _ = img.shape
    print(file_name, img_height, img_width)
    cv2.destroyAllWindows()
    with open(file, 'r') as f:
        lines_list = []
        lines = f.readlines()
        for line in lines:
            line = list(map(float, line.strip().split(' ')))
            class_name = int(line[0])
            x_min, y_min = float(min(line[5], line[7])), float(min(line[6], line[8]))
            x_max, y_max = float(max(line[1], line[3])), float(max(line[2], line[4]))
            x_center, y_center = float(((x_min + x_max) / 2) / img_width), float(((y_min + y_max) / 2) / img_height)
            width, height = abs(x_max - x_min) / img_width, abs(y_max - y_min) / img_height
            print(x_center, y_center, width, height)
            lines_list.append([class_name, x_center, y_center, width, height])
    with open('/content/drive/MyDrive/CarData/valid/' + file_name + '.txt', 'w') as f:
        for line in lines_list:
            f.write(str(line[0]) + ' ' + str(line[1]) + ' ' + str(line[2]) + ' ' + str(line[3]) + ' ' + str(line[4]) + '\n')

In [ ]:
txt_file_list = glob.glob('/content/drive/MyDrive/CarData/train/*.txt')

In [ ]:
for file in tqdm(txt_file_list):
    file_name = os.path.basename(file)
    file_name = file_name.split('.')[0]
    print(file_name)
    img = cv2.imread('/content/drive/MyDrive/CarData/train/' + file_name + '.jpg')
    img_height, img_width, _ = img.shape
    print(file_name, img_height, img_width)
    cv2.destroyAllWindows()
    with open(file, 'r') as f:
        lines_list = []
        lines = f.readlines()
        for line in lines:
            line = list(map(float, line.strip().split(' ')))
            if not len(line) == 9:
               break
            class_name = int(line[0])
            x_min, y_min = float(min(line[5], line[7])), float(min(line[6], line[8]))
            x_max, y_max = float(max(line[1], line[3])), float(max(line[2], line[4]))
            x_center, y_center = float(((x_min + x_max) / 2) / img_width), float(((y_min + y_max) / 2) / img_height)
            width, height = abs(x_max - x_min) / img_width, abs(y_max - y_min) / img_height
            print(x_center, y_center, width, height)
            lines_list.append([class_name, x_center, y_center, width, height])
    if not len(line) == 9:
       continue
    with open('/content/drive/MyDrive/CarData/train/' + file_name + '.txt', 'w') as f:
        for line in lines_list:
            f.write(str(line[0]) + ' ' + str(line[1]) + ' ' + str(line[2]) + ' ' + str(line[3]) + ' ' + str(line[4]) + '\n')

  0%|          | 3/5833 [00:00<03:41, 26.29it/s]

syn_05799
syn_05799 1040 1920
syn_05801
syn_05801 1040 1920
syn_05804
syn_05804 1040 1920
syn_05803
syn_05803 1040 1920
syn_05805
syn_05805 1040 1920
syn_05800


  0%|          | 9/5833 [00:00<03:40, 26.43it/s]

syn_05800 1040 1920
syn_05802
syn_05802 1040 1920
syn_05797
syn_05797 1040 1920
syn_05798
syn_05798 1040 1920
syn_05815
syn_05815 1040 1920
syn_05812
syn_05812 1040 1920
syn_05814


  0%|          | 15/5833 [00:00<03:39, 26.51it/s]

...

syn_00781 1040 1920
0.43854166666666666 0.3216346153846154 0.15104166666666666 0.34134615384615385
0.24973958333333332 0.4115384615384615 0.1359375 0.28846153846153844
syn_00782
syn_00782 1040 1920
0.65859375 0.48990384615384613 0.15885416666666666 0.30096153846153845
0.42578125 0.3942307692307692 0.12239583333333333 0.2519230769230769
0.22682291666666668 0.4125 0.12864583333333332 0.2826923076923077
syn_00786
syn_00786 1040 1920
0.62890625 0.35096153846153844 0.16197916666666667 0.3
0.44557291666666665 0.38846153846153847 0.16614583333333333 0.3326923076923077
0.22265625 0.3173076923076923 0.1359375 0.26346153846153847
syn_00780
syn_00780 1040 1920
0.6596354166666667 0.5216346153846154 0.13802083333333334 0.2644230769230769
0.48489583333333336 0.6365384615384615 0.15416666666666667 0.3096153846153846
0.2669270833333333 0.6495192307692308 0.1640625 0.3778846153846154
syn_05775
syn_05775 1040 1920
0.6848958333333334 0.49230769230769234 0.153125 0.27692307692307694
0.5096354166666667 0.6

100%|█████████▉| 5828/5833 [04:08<00:00, 17.57it/s]

syn_05772 1040 1920
0.6106770833333334 0.42451923076923076 0.14322916666666666 0.24519230769230768
0.44479166666666664 0.5288461538461539 0.12708333333333333 0.2673076923076923
0.25286458333333334 0.5995192307692307 0.15677083333333333 0.35865384615384616
syn_05773
syn_05773 1040 1920
0.45364583333333336 0.5086538461538461 0.13229166666666667 0.2673076923076923
0.23984375 0.5153846153846153 0.14322916666666666 0.28846153846153844
syn_05781
syn_05781 1040 1920
0.6526041666666667 0.5014423076923077 0.15 0.2548076923076923
0.4627604166666667 0.5389423076923077 0.14322916666666666 0.2721153846153846
0.22291666666666668 0.3716346153846154 0.12708333333333333 0.24519230769230768
syn_05785
syn_05785 1040 1920
0.6265625 0.4355769230769231 0.15208333333333332 0.25576923076923075
0.38984375 0.26346153846153847 0.14114583333333333 0.28076923076923077
0.20572916666666666 0.3245192307692308 0.12604166666666666 0.24134615384615385
syn_05779
syn_05779 1040 1920
0.5927083333333333 0.2668269230769231 0

100%|██████████| 5833/5833 [04:09<00:00, 23.42it/s]

syn_05777 1040 1920
0.66171875 0.5423076923076923 0.16302083333333334 0.27692307692307694
0.42864583333333334 0.43990384615384615 0.14583333333333334 0.2701923076923077
0.24270833333333333 0.5389423076923077 0.13333333333333333 0.30288461538461536
syn_05783
syn_05783 1040 1920
0.6486979166666667 0.4596153846153846 0.15260416666666668 0.28846153846153844
0.45078125 0.47836538461538464 0.1390625 0.25096153846153846
0.25677083333333334 0.5288461538461539 0.13020833333333334 0.275
syn_05791
syn_05791 1040 1920
0.6296875 0.40048076923076925 0.14479166666666668 0.24519230769230768
0.4557291666666667 0.48028846153846155 0.14895833333333333 0.26826923076923076
0.22083333333333333 0.33076923076923076 0.125 0.23846153846153847
syn_05789
syn_05789 1040 1920
0.46380208333333334 0.47836538461538464 0.16302083333333334 0.33942307692307694
0.24869791666666666 0.4754807692307692 0.1203125 0.2625
syn_05787
syn_05787 1040 1920
0.6486979166666667 0.46971153846153846 0.15572916666666667 0.2625
0.449739583

# 데이터 준비
- darknet/data/obj에 압축 풀기
- classes.names와 training.data 파일 생성
- training.txt 파일 생성

In [ ]:
!zip -r '/content/drive/MyDrive/CarData.zip' '/content/drive/MyDrive/CarData'

Streaming output truncated to the last 5000 lines.
updating: content/drive/MyDrive/CarData/train/syn_05352.txt (deflated 57%)
updating: content/drive/MyDrive/CarData/train/syn_05359.txt (deflated 56%)
updating: content/drive/MyDrive/CarData/train/syn_05355.txt (deflated 53%)
updating: content/drive/MyDrive/CarData/train/syn_05360.txt (deflated 55%)
updating: content/drive/MyDrive/CarData/train/syn_05357.txt (deflated 55%)
updating: content/drive/MyDrive/CarData/train/syn_05353.txt (deflated 26%)
updating: content/drive/MyDrive/CarData/train/syn_05368.txt (deflated 58%)
updating: content/drive/MyDrive/CarData/train/syn_05363.txt (deflated 52%)
updating: content/drive/MyDrive/CarData/train/syn_05364.txt (deflated 56%)
updating: content/drive/MyDrive/CarData/train/syn_05365.txt (deflated 58%)
updating: content/drive/MyDrive/CarData/train/syn_05362.txt (deflated 55%)
updating: content/drive/MyDrive/CarData/train/syn_05367.txt (deflated 57%)
updating: content/drive/MyDrive/CarData/train/syn

In [8]:
!cp /content/drive/MyDrive/CarData.zip ./

In [9]:
!rm -rf data/obj
!mkdir data/obj
# !zip -FF Cars --out Cars_ver2.zip
!unzip CarData.zip -d data/obj

Streaming output truncated to the last 5000 lines.
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05356.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05352.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05359.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05355.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05360.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05357.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05353.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05368.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05363.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05364.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05365.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn_05362.txt  
  inflating: data/obj/content/drive/MyDrive/CarData/train/syn

In [8]:
pwd

'/content/darknet'

In [10]:
!mv ./data/obj/content/drive/MyDrive/CarData/train ./data/obj
!mv ./data/obj/content/drive/MyDrive/CarData/valid ./data/obj

In [11]:
!rm -r ./data/obj/content/

### 학습 위한 설정 파일 생성

#### data/obj.names

In [12]:
%%writefile data/obj.names
chevrolet_malibu_sedan_2012_2016
chevrolet_malibu_sedan_2017_2019
chevrolet_spark_hatchback_2016_2021
chevrolet_trailblazer_suv_2021_
chevrolet_trax_suv_2017_2019
genesis_g80_sedan_2016_2020
genesis_g80_sedan_2021_
genesis_gv80_suv_2020_
hyundai_avante_sedan_2011_2015
hyundai_avante_sedan_2020_
hyundai_grandeur_sedan_2011_2016
hyundai_grandstarex_van_2018_2020
hyundai_ioniq_hatchback_2016_2019
hyundai_sonata_sedan_2004_2009
hyundai_sonata_sedan_2010_2014
hyundai_sonata_sedan_2019_2020
kia_carnival_van_2015_2020
kia_carnival_van_2021_
kia_k5_sedan_2010_2015
kia_k5_sedan_2020_
kia_k7_sedan_2016_2020
kia_mohave_suv_2020_
kia_morning_hatchback_2004_2010
kia_morning_hatchback_2011_2016
kia_ray_hatchback_2012_2017
kia_sorrento_suv_2015_2019
kia_sorrento_suv_2020_
kia_soul_suv_2014_2018
kia_sportage_suv_2016_2020
kia_stonic_suv_2017_2019
renault_sm3_sedan_2015_2018
renault_xm3_suv_2020_
ssangyong_korando_suv_2019_2020
ssangyong_tivoli_suv_2016_2020

Writing data/obj.names


In [13]:
!cat data/obj.names

chevrolet_malibu_sedan_2012_2016
chevrolet_malibu_sedan_2017_2019
chevrolet_spark_hatchback_2016_2021
chevrolet_trailblazer_suv_2021_
chevrolet_trax_suv_2017_2019
genesis_g80_sedan_2016_2020
genesis_g80_sedan_2021_
genesis_gv80_suv_2020_
hyundai_avante_sedan_2011_2015
hyundai_avante_sedan_2020_
hyundai_grandeur_sedan_2011_2016
hyundai_grandstarex_van_2018_2020
hyundai_ioniq_hatchback_2016_2019
hyundai_sonata_sedan_2004_2009
hyundai_sonata_sedan_2010_2014
hyundai_sonata_sedan_2019_2020
kia_carnival_van_2015_2020
kia_carnival_van_2021_
kia_k5_sedan_2010_2015
kia_k5_sedan_2020_
kia_k7_sedan_2016_2020
kia_mohave_suv_2020_
kia_morning_hatchback_2004_2010
kia_morning_hatchback_2011_2016
kia_ray_hatchback_2012_2017
kia_sorrento_suv_2015_2019
kia_sorrento_suv_2020_
kia_soul_suv_2014_2018
kia_sportage_suv_2016_2020
kia_stonic_suv_2017_2019
renault_sm3_sedan_2015_2018
renault_xm3_suv_2020_
ssangyong_korando_suv_2019_2020
ssangyong_tivoli_suv_2016_2020


In [14]:
!cp data/obj.names data/coco.names


### data/obj.data

In [15]:
%%writefile data/obj.data
classes = 34
train = data/train.txt
valid = data/valid.txt
names = /content/darknet/data/obj.names
backup = ./

Writing data/obj.data


In [36]:
pwd

'/content/darknet'

In [16]:
!cat data/obj.data

classes = 34
train = data/train.txt
valid = data/valid.txt
names = /content/darknet/data/obj.names
backup = ./


### data/train.txt

In [17]:
!ls -al data/obj/train

total 5183500
drwx------ 2 root root  434176 Jun  6 14:40 .
drwxr-xr-x 4 root root    4096 Jun  7 10:05 ..
-rw------- 1 root root  994024 Jun  4 17:23 syn_00023.jpg
-rw------- 1 root root     244 Jun  6 14:39 syn_00023.txt
-rw------- 1 root root  839809 Jun  4 17:23 syn_00024.jpg
-rw------- 1 root root     214 Jun  6 14:39 syn_00024.txt
-rw------- 1 root root  960370 Jun  4 17:23 syn_00025.jpg
-rw------- 1 root root     219 Jun  6 14:39 syn_00025.txt
-rw------- 1 root root 1059879 Jun  4 17:23 syn_00026.jpg
-rw------- 1 root root     207 Jun  6 14:39 syn_00026.txt
-rw------- 1 root root  928339 Jun  4 17:23 syn_00027.jpg
-rw------- 1 root root     154 Jun  6 14:39 syn_00027.txt
-rw------- 1 root root  968180 Jun  4 17:23 syn_00028.jpg
-rw------- 1 root root     214 Jun  6 14:39 syn_00028.txt
-rw------- 1 root root  721928 Jun  4 17:23 syn_00029.jpg
-rw------- 1 root root     199 Jun  6 14:39 syn_00029.txt
-rw------- 1 root root 1099528 Jun  4 17:23 syn_00030.jpg
-rw------- 1 root root 

In [18]:
# ls -al data/obj/Raccoon 밑에 jpg 파일들이 있으면
# images_list = glob.glob("data/obj/laptops_labeled/*[jpg|png|jpeg]")
images_list_1 = glob.glob("data/obj/train/*[jpg|png|jpeg]")
images_list_2 = glob.glob("data/obj/valid/*[jpg|png|jpeg]")

# ls -al data/obj 밑에 jpg 파일들이 있으면
# images_list = glob.glob("data/obj/*[jpg|png|jpeg]")

print(images_list_1)
print(images_list_2)

# Create train.txt file
file = open("data/train.txt", "w") 
file.write("\n".join(images_list_1)) 
file.close() 

file = open("data/valid.txt", "w") 
file.write("\n".join(images_list_2)) 
file.close() 

['data/obj/train/syn_05266.jpg', 'data/obj/train/syn_03938.jpg', 'data/obj/train/syn_03461.jpg', 'data/obj/train/syn_00801.jpg', 'data/obj/train/syn_05050.jpg', 'data/obj/train/syn_00525.jpg', 'data/obj/train/syn_00658.jpg', 'data/obj/train/syn_03941.jpg', 'data/obj/train/syn_01429.jpg', 'data/obj/train/syn_05647.jpg', 'data/obj/train/syn_01279.jpg', 'data/obj/train/syn_01406.jpg', 'data/obj/train/syn_03282.jpg', 'data/obj/train/syn_05057.jpg', 'data/obj/train/syn_00990.jpg', 'data/obj/train/syn_02292.jpg', 'data/obj/train/syn_04717.jpg', 'data/obj/train/syn_04086.jpg', 'data/obj/train/syn_00271.jpg', 'data/obj/train/syn_00070.jpg', 'data/obj/train/syn_03299.jpg', 'data/obj/train/syn_00689.jpg', 'data/obj/train/syn_01860.jpg', 'data/obj/train/syn_04624.jpg', 'data/obj/train/syn_01157.jpg', 'data/obj/train/syn_05434.jpg', 'data/obj/train/syn_01037.jpg', 'data/obj/train/syn_04636.jpg', 'data/obj/train/syn_01824.jpg', 'data/obj/train/syn_04843.jpg', 'data/obj/train/syn_04354.jpg', 'data/o

In [19]:
!cat data/train.txt

data/obj/train/syn_05266.jpg
data/obj/train/syn_03938.jpg
data/obj/train/syn_03461.jpg
data/obj/train/syn_00801.jpg
data/obj/train/syn_05050.jpg
data/obj/train/syn_00525.jpg
data/obj/train/syn_00658.jpg
data/obj/train/syn_03941.jpg
data/obj/train/syn_01429.jpg
data/obj/train/syn_05647.jpg
data/obj/train/syn_01279.jpg
data/obj/train/syn_01406.jpg
data/obj/train/syn_03282.jpg
data/obj/train/syn_05057.jpg
data/obj/train/syn_00990.jpg
data/obj/train/syn_02292.jpg
data/obj/train/syn_04717.jpg
data/obj/train/syn_04086.jpg
data/obj/train/syn_00271.jpg
data/obj/train/syn_00070.jpg
data/obj/train/syn_03299.jpg
data/obj/train/syn_00689.jpg
data/obj/train/syn_01860.jpg
data/obj/train/syn_04624.jpg
data/obj/train/syn_01157.jpg
data/obj/train/syn_05434.jpg
data/obj/train/syn_01037.jpg
data/obj/train/syn_04636.jpg
data/obj/train/syn_01824.jpg
data/obj/train/syn_04843.jpg
data/obj/train/syn_04354.jpg
data/obj/train/syn_05717.jpg
data/obj/train/syn_05072.jpg
data/obj/train/syn_03144.jpg
data/obj/train

# 4. 사전 학습된 YOLOv3 모델 파일 다운로드

In [20]:
# !wget https://pjreddie.com/media/files/yolov3.weights
!wget https://pjreddie.com/media/files/darknet53.conv.74
# !wget https://github.com/AlexeyAB/darknet/releases/download/darknet_yolo_v4_pre/yolov4_tiny.conv.29

--2023-06-07 10:05:28--  https://pjreddie.com/media/files/darknet53.conv.74
Resolving pjreddie.com (pjreddie.com)... 128.208.4.108
Connecting to pjreddie.com (pjreddie.com)|128.208.4.108|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 162482580 (155M) [application/octet-stream]
Saving to: ‘darknet53.conv.74’

darknet53.conv.74   100%[===================>] 154.96M  18.2MB/s    in 9.5s    

2023-06-07 10:05:38 (16.3 MB/s) - ‘darknet53.conv.74’ saved [162482580/162482580]



# 5. 학습관련 설정 파일 수정

원 설정파일 yolov3.cfg를 yolv3_custom.cfg로 복사하고

복사한 설정파일을 수정

In [21]:
# 탐지 대상 클래스 수를 설정
CLASS_NUM = 34

In [22]:
!cp cfg/yolov3.cfg cfg/yolov3_custom.cfg

classes = 34
filters = 117 # (classes + 5) * 3
# max_batches = classes * 2000
max_batches = 34000 # classes * 1000
steps1 = 27200 # int(max_batches*0.8)
steps2 = 30600 # int(max_batches*0.9)
# if max_batches < 6000:
#   max_batches = 6000

# Edit classes & filters
!sed -i 's/batch=1/batch=64/' cfg/yolov3_custom.cfg
!sed -i 's/subdivisions=1/subdivisions=32/' cfg/yolov3_custom.cfg
!sed -i 's/max_batches = 500200/max_batches = $max_batches/' cfg/yolov3_custom.cfg
!sed -i '610 s@classes=80@classes=$classes@' cfg/yolov3_custom.cfg
!sed -i '696 s@classes=80@classes=$classes@' cfg/yolov3_custom.cfg
!sed -i '783 s@classes=80@classes=$classes@' cfg/yolov3_custom.cfg
!sed -i '603 s@filters=255@filters=$filters@' cfg/yolov3_custom.cfg
!sed -i '689 s@filters=255@filters=$filters@' cfg/yolov3_custom.cfg
!sed -i '776 s@filters=255@filters=$filters@' cfg/yolov3_custom.cfg
!sed -i 's/steps=400000,450000/steps=$steps1,$steps2/' cfg/yolov3_custom.cfg

# 6. 학습 실행

학습된 모델은  ./yolov3_custom_last.weights 로 저장된다.

In [26]:
!mv /content/drive/MyDrive/yolov3_custom.cfg /content/darknet/cfg 

In [ ]:
pwd

'/content/darknet'

In [27]:
!./darknet detector train data/obj.data cfg/yolov3_custom.cfg darknet53.conv.74 -dont_show # 학습 중지는 컨트롤씨

Streaming output truncated to the last 5000 lines.
v3 (mse loss, Normalizer: (iou: 0.75, obj: 1.00, cls: 1.00) Region 106 Avg (IOU: 0.000000), count: 1, class_loss = 0.000026, iou_loss = 0.000000, total_loss = 0.000026 
 total_bbox = 202484, rewritten_bbox = 0.000000 % 
v3 (mse loss, Normalizer: (iou: 0.75, obj: 1.00, cls: 1.00) Region 82 Avg (IOU: 0.532767), count: 3, class_loss = 1.058751, iou_loss = 1.375792, total_loss = 2.434543 
v3 (mse loss, Normalizer: (iou: 0.75, obj: 1.00, cls: 1.00) Region 94 Avg (IOU: 0.770191), count: 2, class_loss = 0.376241, iou_loss = 0.210455, total_loss = 0.586696 
v3 (mse loss, Normalizer: (iou: 0.75, obj: 1.00, cls: 1.00) Region 106 Avg (IOU: 0.000000), count: 1, class_loss = 0.000002, iou_loss = 0.000000, total_loss = 0.000002 
 total_bbox = 202489, rewritten_bbox = 0.000000 % 
v3 (mse loss, Normalizer: (iou: 0.75, obj: 1.00, cls: 1.00) Region 82 Avg (IOU: 0.549233), count: 2, class_loss = 0.011810, iou_loss = 0.595415, total_loss = 0.607225 
v3 (m

In [30]:
!cp ./yolov3_custom_last.weights /content/drive/MyDrive/

## 7. 탐지 실행

In [32]:
!./darknet detect cfg/yolov3_custom.cfg ./yolov3_custom_last.weights data/obj/valid/syn_00000.jpg

 CUDA-version: 11080 (12000), cuDNN: 8.7.0, GPU count: 1  
 OpenCV version: 4.2.0
 0 : compute_capability = 750, cudnn_half = 0, GPU: Tesla T4 
net.optimized_memory = 0 
mini_batch = 1, batch = 32, time_steps = 1, train = 0 
   layer   filters  size/strd(dil)      input                output
   0 Create CUDA-stream - 0 
 Create cudnn-handle 0 
conv     32       3 x 3/ 1    416 x 416 x   3 ->  416 x 416 x  32 0.299 BF
   1 conv     64       3 x 3/ 2    416 x 416 x  32 ->  208 x 208 x  64 1.595 BF
   2 conv     32       1 x 1/ 1    208 x 208 x  64 ->  208 x 208 x  32 0.177 BF
   3 conv     64       3 x 3/ 1    208 x 208 x  32 ->  208 x 208 x  64 1.595 BF
   4 Shortcut Layer: 1,  wt = 0, wn = 0, outputs: 208 x 208 x  64 0.003 BF
   5 conv    128       3 x 3/ 2    208 x 208 x  64 ->  104 x 104 x 128 1.595 BF
   6 conv     64       1 x 1/ 1    104 x 104 x 128 ->  104 x 104 x  64 0.177 BF
   7 conv    128       3 x 3/ 1    104 x 104 x  64 ->  104 x 104 x 128 1.595 BF
   8 Shortcut Layer: 5, 

In [34]:
pred = plt.imread('predictions.jpg')
plt.figure(figsize=(10,10))
plt.imshow(pred)
plt.show()